In [61]:
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import math

def truncate(number, decimals=0):
    """
    Returns a value truncated to a specific number of decimal places.
    """
    if not isinstance(decimals, int):
        raise TypeError("decimal places must be an integer.")
    elif decimals < 0:
        raise ValueError("decimal places has to be 0 or more.")
    elif decimals == 0:
        return math.trunc(number)

    factor = 10.0 ** decimals
    return math.trunc(number * factor) / factor

def get_hist(ax):
    n,bins = [],[]
    for rect in ax.patches:
        ((x0, y0), (x1, y1)) = rect.get_bbox().get_points()
        n.append(y1-y0)
        bins.append(x0) # left edge of each bin
        bins.append(x1) # also get right edge of last bin

    return n,bins


#read csv file and labels columns 
df_czt = pd.read_csv('board1.unpacked', header=None, sep='\s+', engine='python')
df_czt.columns = ['node', 'board', 'Rena', 'channel', 'polarity', 'ADC_e', 'ADC_s', 'ADC_v', 'counter']

print(df_czt.head())

#grouping by multiple columns 
grouped = df_czt.groupby(['node','board','Rena','channel','polarity'])

n_sub_plots_cols = 2
n_sub_plots_rows = math.ceil(grouped.ngroups/n_sub_plots_cols)

fig, axes = plt.subplots(n_sub_plots_rows, n_sub_plots_cols, figsize=(100,400))
fig.subplots_adjust(hspace=3.0, wspace=1.2)
axes_list = [item for sublist in axes for item in sublist] 

#export these values to excel
export_vals = []

#plot column ADC energy
for key,group in grouped:
    ax = axes_list.pop(0)
    grouped.get_group(key)['ADC_e'].plot(kind='hist', bins=50, ax=ax)
    
    # n = y [counts], bins = x [adc_e]
    n, bins = get_hist(ax)
    #print(n)
    #print(bins)
    #print(len(n))
    #print(len(bins))
    #break
    czt_values = grouped.get_group(key).values[0]
    
    #min and max 
    max_val = grouped.get_group(key)['ADC_e'].max()
    min_val = grouped.get_group(key)['ADC_e'].min()
    y_min, y_max = ax.get_ylim()
    ax.annotate('Max: ' +str(max_val), xy=(3, y_max -(y_max * 0.1)), size=80)
    ax.annotate('Min: ' +str(min_val), xy=(3, y_max -(y_max * 0.2)), size=80)
    
    # FWHM DIRECT
    #y_peak = max(n)
    #half_y_peak = y_peak / 2
    #nearest = (np.abs(n - half_y_peak).argmin())
    #peak_index = n.index(y_peak)
    #fwhm = np.abs(bins[nearest] - bins[peak_index]) * 2
    #ax.annotate('FWHM: ' +str(fwhm), xy=(3, y_max -(y_max * 0.3)), size=80) 
    
    # FWHM Gaussian
    y_fwhm = np.array(n)
    temp = []
    flag = 0;
    for i in bins:
        if flag == 0:
            temp.append(i)
            flag = 1
        else:
            flag = 0
    x_fwhm = np.array(temp)
    n_fwhm = len(x_fwhm)                          #the number of data
    mean_fwhm = sum(x_fwhm*y_fwhm)/sum(y_fwhm)    #the mean value of the data
    sigma_fwhm = np.sqrt(sum(y_fwhm * (x_fwhm - mean_fwhm)**2) / sum(y_fwhm)) #standard deviation of the data   
    fwhm = sigma_fwhm * 2.355
    fwhm = truncate(fwhm, 3)
    ax.annotate('FWHM: ' +str(fwhm), xy=(3, y_max -(y_max * 0.3)), size=80)  
    
    export_vals.append((czt_values[2],czt_values[3],fwhm))
    
    
    #titles
    title = "Node:" + str(czt_values[0]) + " Board:"+ str(czt_values[1]) + " Rena:"+ str(czt_values[2]) + " Channel:"+ str(czt_values[3])
    ax.set_title(title, fontsize=80)
    
    #x and y axis labels
    ax.set_xlabel("ADC value", fontsize=80)
    ax.set_ylabel("Counts", fontsize=80)
    
    ax.tick_params(labelsize=50)
    
    ax.autoscale(enable=True, axis='y', tight= False)
    ax.set_xlim(left=0)
    
    #anode or cathode
    if czt_values[4] == 0: 
        ax.set_xlim(right=3450)
    else:
        if czt_values[2] == 1: 
            ax.set_xlim(right=3500)
        else: 
            ax.set_xlim(right=3500)
    

for ax in axes_list:
    ax.remove()

# create a dataframe for export values
export_val_df = pd.DataFrame(export_vals, columns = ['Rena', 'Channel', 'FWHM'])
export_val_df.to_csv('export_data_board1.csv', index=False)

plt.tight_layout()
plt.show()


   node  board  Rena  channel  polarity  ADC_e  ADC_s  ADC_v      counter
0     1     16     0        4         1   2324   2051   2065  54117717569
1     1     16     0        5         1   2344   2054   2041  54117717569
2     1     16     0        6         1   2315   2039   2028  54117717569
3     1     16     0        7         1   2294   2047   2040  54117717569
4     1     16     0        8         1   2290   2054   2036  54117717569


In [30]:
test = truncate(fwhm, 3)

In [31]:
test

22.154